In [1]:
import functools
import json
import os
import tensorflow as tf

from object_detection import trainer
from object_detection.builders import dataset_builder
from object_detection.builders import graph_rewriter_builder
from object_detection.builders import model_builder
from object_detection.utils import config_util
from object_detection.utils import dataset_util

/home/ye/user/yejg/SW_DATA/Or/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


## parameters

In [7]:
# 'Name of the TensorFlow master to use.'
master=''
# 'task id'
task=0
#'Number of clones to deploy per worker.'
num_clones=1

clone_on_cpu=False
# 'Number of worker+trainer 
worker_replicas=1
#'Number of parameter server tasks. If None, does not use '
ps_tasks=0
#  'Directory to save the checkpoints and training summaries.'
train_dir='./object_detection/training/'
#  'Path to a pipeline_pb2.TrainEvalPipelineConfig config '
pipeline_config_path='./object_detection/training/ssd_mobilenet_v1_coco.config'
#  'Path to a train_pb2.TrainConfig config file.'
## train_config_path
#  'Path to an input_reader_pb2.InputReader config file.'
## input_config_path
# 'Path to a model_pb2.DetectionModel config file.'
## model_config_path

In [8]:
def main():
  global task,num_clones,master,worker_replicasr,ps_tasks,train_di,pipeline_config_path,train_config_path,\
         model_config_path,input_config_path
  #assert train_dir==''
  if task == 0: 
        tf.gfile.MakeDirs(train_dir)
  if pipeline_config_path:
    configs = config_util.get_configs_from_pipeline_file(
        pipeline_config_path)
    if task == 0:
      tf.gfile.Copy(pipeline_config_path,
                    os.path.join(train_dir, 'pipeline.config'),
                    overwrite=True)
  else:
    configs = config_util.get_configs_from_multiple_files(
        model_config_path=model_config_path,
        train_config_path=train_config_path,
        train_input_config_path=input_config_path)
    if FLAGS.task == 0:
      for name, config in [('model.config', model_config_path),
                           ('train.config', train_config_path),
                           ('input.config', input_config_path)]:
        tf.gfile.Copy(config, os.path.join(train_dir, name),
                      overwrite=True)

  model_config = configs['model']
  train_config = configs['train_config']
  input_config = configs['train_input_config']

  model_fn = functools.partial(
      model_builder.build,
      model_config=model_config,
      is_training=True)

  def get_next(config):
    return dataset_util.make_initializable_iterator(
        dataset_builder.build(config)).get_next()

  create_input_dict_fn = functools.partial(get_next, input_config)

  env = json.loads(os.environ.get('TF_CONFIG', '{}'))
  cluster_data = env.get('cluster', None)
  cluster = tf.train.ClusterSpec(cluster_data) if cluster_data else None
  task_data = env.get('task', None) or {'type': 'master', 'index': 0}
  task_info = type('TaskSpec', (object,), task_data)

  # Parameters for a single worker.
  ps_tasks = 0
  worker_replicas = 1
  worker_job_name = 'lonely_worker'
  task = 0
  is_chief = True
  master = ''

  if cluster_data and 'worker' in cluster_data:
    # Number of total worker replicas include "worker"s and the "master".
    worker_replicas = len(cluster_data['worker']) + 1
  if cluster_data and 'ps' in cluster_data:
    ps_tasks = len(cluster_data['ps'])

  if worker_replicas > 1 and ps_tasks < 1:
    raise ValueError('At least 1 ps task is needed for distributed training.')

  if worker_replicas >= 1 and ps_tasks > 0:
    # Set up distributed training.
    server = tf.train.Server(tf.train.ClusterSpec(cluster), protocol='grpc',
                             job_name=task_info.type,
                             task_index=task_info.index)
    if task_info.type == 'ps':
      server.join()
      return

    worker_job_name = '%s/task:%d' % (task_info.type, task_info.index)
    task = task_info.index
    is_chief = (task_info.type == 'master')
    master = server.target

  graph_rewriter_fn = None
  if 'graph_rewriter_config' in configs:
    graph_rewriter_fn = graph_rewriter_builder.build(
        configs['graph_rewriter_config'], is_training=True)

  trainer.train(
      create_input_dict_fn,
      model_fn,
      train_config,
      master,
      task,
      num_clones,
      worker_replicas,
      clone_on_cpu,
      ps_tasks,
      worker_job_name,
      is_chief,
      train_dir,
      graph_hook_fn=graph_rewriter_fn)

In [ ]:
if __name__=='__main__':
    main()

INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0


Instructions for updating:
Please switch to tf.train.MonitoredTrainingSession


Instructions for updating:
Please switch to tf.train.MonitoredTrainingSession


INFO:tensorflow:Restoring parameters from /home/ye/user/yejg/LEARN/DL_MODEL_LEARN/objdectect/models/research/object_detection/ssd_mobilenet_v1_coco_2017_11_17/model.ckpt


INFO:tensorflow:Restoring parameters from /home/ye/user/yejg/LEARN/DL_MODEL_LEARN/objdectect/models/research/object_detection/ssd_mobilenet_v1_coco_2017_11_17/model.ckpt


...

INFO:tensorflow:global step 18664: loss = 2.0207 (2.321 sec/step)


INFO:tensorflow:global step 18665: loss = 2.2380 (3.672 sec/step)


INFO:tensorflow:global step 18665: loss = 2.2380 (3.672 sec/step)


INFO:tensorflow:global step 18666: loss = 2.2995 (5.964 sec/step)


INFO:tensorflow:global step 18666: loss = 2.2995 (5.964 sec/step)
